In [4]:
import pandas as pd
import xlwings as xw
import openpyxl as op
import numpy as np
import datetime as dt
import numpy as np
import os

In [3]:
a=pd.DataFrame({'a':[1,2],
               'b':[3,4],
               'c':[5,6]})

In [4]:
a

a  b  c
0  1  3  5
1  2  4  6

In [6]:
#dá uma lista com tds os clubes de uma época de uma liga
#teams é o número de equipas q tem a liga
def findall_clubs(path,teams):
    import pandas as pd
    file=pd.read_excel(path+'.xlsx')
    lista_c=[]
    counter=0
    i=0
    done=False
    while i<len(file.index) and not(done):
        if i==teams+50:
            print('Está a ver demasiadas linhas, tem erro')
        if file.iloc[i]['HomeTeam'] in lista_c:
            pass
        else:
            lista_c+=[file.iloc[i]['HomeTeam']]
            counter+=1
        if file.iloc[i]['AwayTeam'] in lista_c:
            pass
        else:
            lista_c+=[file.iloc[i]['AwayTeam']]
            counter+=1
        if counter==teams:
            done=True
        i+=1
    return lista_c 

_________

# Modelo SVM Won/NotWon (Lion)
Focando-se na equipa com Odd mais baixa

In [17]:
prem=pd.read_excel('PLBeast.xlsx',0)

In [20]:
lion=pd.DataFrame()

In [21]:
lion['Div']=prem['Div']
lion['Date']=prem['Date']
lion['Time']=prem['Time']
#lion['teste']=[1,2,3]

In [ ]:
    s_=[]
    st=[]
    g=[]
    for f in range(x):
        s_+=[0] #nos primeiros x jogos não há média 
        st+=[0]
        g+=[0]
    limit=len(file.index)
    for s in range(x,limit):
        ind=list(range(s-x,s))
        s1=[file.iloc[n]['Shots'] for n in ind]
        st1=[file.iloc[n]['ShotsTarget'] for n in ind]
        g1=[file.iloc[n]['Goals'] for n in ind]
        s_+=[round(sum(s1)/x,2)]
        st+=[round(sum(st1)/x,2)]
        g+=[round(sum(g1)/x,2)]
    file['Shots_'+str(x)]=s_
    file['ShotsTarget_'+str(x)]=st
    file['Goals_'+str(x)]=g
    return file


In [37]:
#devolve lista de equipas com odd mais baixa e mais alta num jogo
def oddlists(file,h_a=5):
    limit=len(file.index)
    l=[] #lista das odds baixas
    h=[] #lista das odds altas
    ha=[] #se a equipa com lowest_odd joga em casa (ha) ou fora (0)
    draw_odd=[] #lista das odds de empate
    s_=[[],[]] #lista da média de shots (casa/fora)
    st=[[],[]] #lista da média de shotstarget (casa/fora)
    g=[[],[]] #lista de média de golos (casa/fora)
    for i in range(limit):
        if file.iloc[i]['Lowest_Odd']=='H': 
            l+=[file.iloc[i]['HomeTeam']]
            h+=[file.iloc[i]['AwayTeam']]
            ha+=[h_a]
            draw_odd+=[file.iloc[i]['ODDD_Aver.']]
        else:
            l+=[file.iloc[i]['AwayTeam']]
            h+=[file.iloc[i]['HomeTeam']]
            ha+=[0]
            draw_odd+=[file.iloc[i]['ODDD_Aver.']]
    return [l,draw_odd,h,ha]

#esta função vai ficar em stanby

In [33]:
oddlists(prem)

[['Liverpool',
  'Man City',
  'Bournemouth',
  'Burnley',
  'Everton',
  'Watford',
  'Tottenham',
  'Leicester',
  'Arsenal',
  'Man United',
  'Arsenal',
  'Aston Villa',
  'Brighton',
  'Everton',
  'Norwich',
  'Liverpool',
  'Man City',
  'Sheffield United',
  'Chelsea',
  'Man United',
  'Everton',
  'Chelsea',
  'Brighton',
  'Man United',
  'Leicester',
  'Watford',
  'Liverpool',
  'Man City',
  'Tottenham',
  'Wolves',
  'Man United',
  'Chelsea',
  'Crystal Palace',
  'Leicester',
  'Man City',
  'Newcastle',
  'West Ham',
  'Liverpool',
  'Everton',
  'Arsenal',
  'Liverpool',
  'Brighton',
  'Man United',
  'Sheffield United',
  'Tottenham',
  'Chelsea',
  'Man City',
  'Everton',
  'Arsenal',
  'West Ham',
  'Southampton',
  'Tottenham',
  'Burnley',
  'Everton',
  'Man City',
  'Newcastle',
  'Crystal Palace',
  'Man United',
  'Arsenal',
  'Liverpool',
  'Liverpool',
  'Aston Villa',
  'Bournemouth',
  'Chelsea',
  'Crystal Palace',
  'Tottenham',
  'Wolves',
  'Man Ci

In [27]:
teamssss=oddlists(prem)

In [30]:
lion['LO_Team']=teamssss[0]
lion['HO_Team']=teamssss[1]

In [36]:
a=[[],[]]
a[0]+=[1]
a

[[1], []]

In [123]:
def add_lion(fileN,fileC,clubs,SSTG=True,LowestLost=True,AwayLast=True,Surprise=True,conceed_aver=3,sstg=5,game_points=5,h_a=10,no_surprise=100,surprise_odd=1.4):
    #game_points: qntspontos teve nos último game_point jogos || també uso para saber qnts game_points jogou fora
    #no_surprise é o valor a atribuir aos jogos sem possibilidade de serem surpresa
    #surprise_odd é a odd a partir da qual já não é considerado surpresa
    
    limit=len(fileN.index)
    h=[]
    l=[]
    bigput_low=[[],[],[],[],[],[],[],[],[],[],[],[],[],[]]        #listas que vamos adicionar à df
    bigput_high=[[],[],[],[],[],[],[],[],[],[],[],[],[],[]]
    low_odd=[] #lista das odds + baixas
    high_odd=[] #lista das odds + altas
    HA=[] #equipa odd baixa casa(h_a)/fora(0)
    odds=[0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0] #odd counter (já vai ter counter negativos) (1,2.8,0.1)
    oddsput=[] #põe em coluna
    surprise=0 #counter de jogos surpresa
    surpriseput=[] #põe em coluna
    wonnotwon=[] #coluna Won/NotWon
    
    for club in clubs:                  # último da lista é o counter do clube (qnts jogos já jogou)
        vars()[club]=[[],[],[],[],0,0,0,0,0,0,0,10000,[],[],0] #cada clube tem uma lista de listas (shots/shotstarget/golos/concedidos/ganhos/jogos marca/jogos não concede)
    #[7]/[8]/[9]/[10] são as colunas de s/st/g/concd sem média (referem-se sempre ao jogo anterior)
    #[11] odd mais baixa que tinha e não ganhou (ninguém tem odd 10000, por isso é que lá deixei)
    #[12] pontos 
    #[13] jogos fora (+1fora/+0casa)
    for i in range(limit):                 
        if fileN.iloc[i]['Lowest_Odd']=='H': 
            l+=[fileN.iloc[i]['HomeTeam']]
            h+=[fileN.iloc[i]['AwayTeam']]
            LO=fileN.iloc[i]['HomeTeam']
            HO=fileN.iloc[i]['AwayTeam']
        else:
            l+=[fileN.iloc[i]['AwayTeam']]
            h+=[fileN.iloc[i]['HomeTeam']]
            HO=fileN.iloc[i]['HomeTeam']
            LO=fileN.iloc[i]['AwayTeam']
        
        #     #         #   Trata de criar colunas dos s/st/g/concd normais mas para LO e HO
        
        if vars()[LO][-1]==0:
            bigput_low[7]+=[0]
            bigput_low[8]+=[0]
            bigput_low[9]+=[0]
            bigput_low[10]+=[0]
        elif vars()[LO][-1]>0:
            bigput_low[7]+=[vars()[LO][7]]
            bigput_low[8]+=[vars()[LO][8]]
            bigput_low[9]+=[vars()[LO][9]]
            bigput_low[10]+=[vars()[LO][10]]
        
        if vars()[HO][-1]==0:
            bigput_high[7]+=[0]
            bigput_high[8]+=[0]
            bigput_high[9]+=[0]
            bigput_high[10]+=[0]
        elif vars()[HO][-1]>0:
            bigput_high[7]+=[vars()[HO][7]]
            bigput_high[8]+=[vars()[HO][8]]
            bigput_high[9]+=[vars()[HO][9]]
            bigput_high[10]+=[vars()[HO][10]]
        
        if fileN.iloc[i]['Lowest_Odd']=='H':
            vars()[LO][7]=fileN.iloc[i]['HS']
            vars()[LO][8]=fileN.iloc[i]['HST']
            vars()[LO][9]=fileN.iloc[i]['FTHG']
            vars()[LO][10]=fileN.iloc[i]['FTAG']
            vars()[HO][7]=fileN.iloc[i]['AS']
            vars()[HO][8]=fileN.iloc[i]['AST']
            vars()[HO][9]=fileN.iloc[i]['FTAG']
            vars()[HO][10]=fileN.iloc[i]['FTHG']
            
        elif fileN.iloc[i]['Lowest_Odd']=='A':
            vars()[LO][7]=fileN.iloc[i]['AS']
            vars()[LO][8]=fileN.iloc[i]['AST']
            vars()[LO][9]=fileN.iloc[i]['FTAG']
            vars()[LO][10]=fileN.iloc[i]['FTHG']
            vars()[HO][7]=fileN.iloc[i]['HS']
            vars()[HO][8]=fileN.iloc[i]['HST']
            vars()[HO][9]=fileN.iloc[i]['FTHG']
            vars()[HO][10]=fileN.iloc[i]['FTAG']
            
        #   #     #     #      #      #     #     #     #     #    # 
        #  #  #  Trata da média dos golos concedidos 
        
        if vars()[LO][-1]==0:
            bigput_low[3]+=[0] #se não jogos para fazer média, os primeiros valores são 0
            #neste caso é a média de golos concedidos
        elif 0<vars()[LO][-1]<conceed_aver:
            bigput_low[3]+=[sum(vars()[LO][3])/len(vars()[LO][3])]
        else:
            bigput_low[3]+=[sum(vars()[LO][3][(-(conceed_aver)):])/conceed_aver] 
        if vars()[HO][-1]==0:
            bigput_high[3]+=[0] #se não jogos para fazer média, os primeiros valores são 0
            #neste caso é a média de golos concedidos
        elif 0<vars()[HO][-1]<conceed_aver:
             bigput_high[3]+=[sum(vars()[HO][3])/len(vars()[HO][3])] 
        else:
            bigput_high[3]+=[sum(vars()[HO][3][(-(conceed_aver)):])/conceed_aver] 
            
        if fileN.iloc[i]['Lowest_Odd']=='H':  
            vars()[LO][3]+=[fileN.iloc[i]['FTAG']]
            vars()[HO][3]+=[fileN.iloc[i]['FTHG']]  
        
        elif fileN.iloc[i]['Lowest_Odd']=='A':
            vars()[HO][3]+=[fileN.iloc[i]['FTAG']]
            vars()[LO][3]+=[fileN.iloc[i]['FTHG']]
        
        # #    #    #   #    #    #   #    #    #    #    #  
        ## # Trata dos counter ganhos/marcou/concedeu
        
        if vars()[LO][-1]==0:
            bigput_low[4]+=[0] #no primeiro dia os counter estão tds a zero
            bigput_low[5]+=[0] 
            bigput_low[6]+=[0] 
        if vars()[HO][-1]==0:
            bigput_high[4]+=[0] #no primeiro dia os counter estão tds a zero
            bigput_high[5]+=[0] 
            bigput_high[6]+=[0]
            
            
        if vars()[LO][-1]>0:
            bigput_low[4]+=[vars()[LO][4]] 
            bigput_low[5]+=[vars()[LO][5]] 
            bigput_low[6]+=[vars()[LO][6]] 
        if vars()[HO][-1]>0:
            bigput_high[4]+=[vars()[HO][4]] 
            bigput_high[5]+=[vars()[HO][5]] 
            bigput_high[6]+=[vars()[HO][6]]
            
        #temos de dividir em dois casos: Odd+baixa Casa/Odd+baixa Fora    
        if fileN.iloc[i]['Lowest_Odd']=='H':   #Odd + baixa CASA 
            if fileN.iloc[i]['FTR']=='H': #se a equipa de casa ganha, como fica o counter
                if vars()[LO][4]>0:
                    vars()[LO][4]+=1 
                else:
                    vars()[LO][4]=1
                if vars()[HO][4]>0:
                    vars()[HO][4]=-1 
                else:
                    vars()[HO][4]-=1 
            if fileN.iloc[i]['FTR']=='A': #se a equipa de fora ganha, como fica o counter
                if vars()[LO][4]>0:
                    vars()[LO][4]=-1 
                else:
                    vars()[LO][4]-=1
                if vars()[HO][4]>0:
                    vars()[HO][4]+=1 
                else:
                    vars()[HO][4]=1 
            if fileN.iloc[i]['FTR']=='D': #se há empate, os counter de jogos ganhos vão todos a zero
                if vars()[LO][4]>0:
                    vars()[LO][4]=-1 
                else:
                    vars()[LO][4]-=1
                if vars()[HO][4]>0:
                    vars()[HO][4]=-1 
                else:
                    vars()[HO][4]-=1 
            if fileN.iloc[i]['FTHG']>0 and fileN.iloc[i]['FTAG']>0: # se ambas marcam
                #print('(+,+)')
                if vars()[LO][5]>0:
                    vars()[LO][5]+=1 
                else:
                    vars()[LO][5]=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]+=1    
                else:
                    vars()[HO][5]=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]=-1
                else:
                    vars()[LO][6]-=1
                if vars()[HO][6]>0:
                    vars()[HO][6]=-1 
                else:
                    vars()[HO][6]-=1 
            if fileN.iloc[i]['FTHG']>0 and fileN.iloc[i]['FTAG']==0: # se só casa marca
                #print('(+,0)')
                if vars()[LO][5]>0:
                    vars()[LO][5]+=1 
                else:
                    vars()[LO][5]=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]=-1    
                else:
                    vars()[HO][5]-=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]+=1
                else:
                    vars()[LO][6]=1
                if vars()[HO][6]>0:
                    vars()[HO][6]=-1 
                else:
                    vars()[HO][6]-=1 
            if fileN.iloc[i]['FTHG']==0 and fileN.iloc[i]['FTAG']>0: # se só fora marca
                #print('(0,+)')
                if vars()[LO][5]>0:
                    vars()[LO][5]=-1 
                else:
                    vars()[LO][5]-=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]+=1    
                else:
                    vars()[HO][5]=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]=-1
                else:
                    vars()[LO][6]-=1
                if vars()[HO][6]>0:
                    vars()[HO][6]+=1 
                else:
                    vars()[HO][6]=1 
            if fileN.iloc[i]['FTHG']==0 and fileN.iloc[i]['FTAG']==0: # se nenhuma marca
                #print('(0,0)')
                if vars()[LO][5]>0:
                    vars()[LO][5]=-1 
                else:
                    vars()[LO][5]-=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]=-1    
                else:
                    vars()[HO][5]-=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]+=1
                else:
                    vars()[LO][6]=1
                if vars()[HO][6]>0:
                    vars()[HO][6]+=1 
                else:
                    vars()[HO][6]=1 
        
        if fileN.iloc[i]['Lowest_Odd']=='A': 
            if fileN.iloc[i]['FTR']=='H': #se a equipa de casa ganha, como fica o counter
                if vars()[LO][4]>0:
                    vars()[LO][4]=-1 
                else:
                    vars()[LO][4]-=1
                if vars()[HO][4]>0:
                    vars()[HO][4]+=1 
                else:
                    vars()[HO][4]=1 
            if fileN.iloc[i]['FTR']=='A': #se a equipa de fora ganha, como fica o counter
                if vars()[LO][4]>0:
                    vars()[LO][4]+=1 
                else:
                    vars()[LO][4]=1
                if vars()[HO][4]>0:
                    vars()[HO][4]=-1 
                else:
                    vars()[HO][4]-=1 
            if fileN.iloc[i]['FTR']=='D': #se há empate, os counter de jogos ganhos vão todos a negativo
                if vars()[LO][4]>0:
                    vars()[LO][4]=-1 
                else:
                    vars()[LO][4]-=1
                if vars()[HO][4]>0:
                    vars()[HO][4]=-1 
                else:
                    vars()[HO][4]-=1 
            if fileN.iloc[i]['FTHG']>0 and fileN.iloc[i]['FTAG']>0: # se ambas marcam
                #print('(+,+)')
                if vars()[LO][5]>0:
                    vars()[LO][5]+=1 
                else:
                    vars()[LO][5]=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]+=1    
                else:
                    vars()[HO][5]=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]=-1
                else:
                    vars()[LO][6]-=1
                if vars()[HO][6]>0:
                    vars()[HO][6]=-1 
                else:
                    vars()[HO][6]-=1 
            if fileN.iloc[i]['FTHG']>0 and fileN.iloc[i]['FTAG']==0: # se só casa marca
                #print('(+,0)')
                if vars()[LO][5]>0:
                    vars()[LO][5]=-1 
                else:
                    vars()[LO][5]-=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]+=1    
                else:
                    vars()[HO][5]=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]=-1
                else:
                    vars()[LO][6]-=1
                if vars()[HO][6]>0:
                    vars()[HO][6]+=1 
                else:
                    vars()[HO][6]=1 
            if fileN.iloc[i]['FTHG']==0 and fileN.iloc[i]['FTAG']>0: # se só fora marca
                #print('(0,+)')
                if vars()[LO][5]>0:
                    vars()[LO][5]+=1 
                else:
                    vars()[LO][5]=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]=-1    
                else:
                    vars()[HO][5]-=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]+=1
                else:
                    vars()[LO][6]=1
                if vars()[HO][6]>0:
                    vars()[HO][6]=-1 
                else:
                    vars()[HO][6]-=1 
            if fileN.iloc[i]['FTHG']==0 and fileN.iloc[i]['FTAG']==0: # se nenhuma marca
                #print('(0,0)')
                if vars()[LO][5]>0:
                    vars()[LO][5]=-1 
                else:
                    vars()[LO][5]-=1    
                if vars()[HO][5]>0:
                    vars()[HO][5]=-1    
                else:
                    vars()[HO][5]-=1    
                if vars()[LO][6]>0:
                    vars()[LO][6]+=1
                else:
                    vars()[LO][6]=1
                if vars()[HO][6]>0:
                    vars()[HO][6]+=1 
                else:
                    vars()[HO][6]=1 
        
        
        
        
        #      #       #         #     #    #      #         #    
        # # #      Trata das médias de s/st/g
            
        if vars()[LO][-1]==0:
            bigput_low[0]+=[0] # os primeiros valores são 0
            bigput_low[1]+=[0] 
            bigput_low[2]+=[0] # neste caso é para o shots/shotstarget/goals
        elif 0<vars()[LO][-1]<sstg:
            bigput_low[0]+=[sum(vars()[LO][0])/len(vars()[LO][0])] #vai fazendo médio com os jogos q já existem
            bigput_low[1]+=[sum(vars()[LO][1])/len(vars()[LO][1])] 
            bigput_low[2]+=[sum(vars()[LO][2])/len(vars()[LO][2])]
        elif vars()[LO][-1]>=sstg:
            #print(vars()[LO])
            #print(bigput)
            bigput_low[0]+=[sum(vars()[LO][0][(-(sstg)):])/sstg] 
            bigput_low[1]+=[sum(vars()[LO][1][(-(sstg)):])/sstg] 
            bigput_low[2]+=[sum(vars()[LO][2][(-(sstg)):])/sstg] # neste caso é para o shots/shotstarget/goals
            
        #Agr é para a odd+alta
        if vars()[HO][-1]==0:
            bigput_high[0]+=[0] # os primeiros valores são 0
            bigput_high[1]+=[0] 
            bigput_high[2]+=[0] # neste caso é para o shots/shotstarget/goals
        elif 0<vars()[HO][-1]<sstg:
            bigput_high[0]+=[sum(vars()[HO][0])/len(vars()[HO][0])] #vai fazendo médio com os jogos q já existem
            bigput_high[1]+=[sum(vars()[HO][1])/len(vars()[HO][1])] 
            bigput_high[2]+=[sum(vars()[HO][2])/len(vars()[HO][2])]
        elif vars()[HO][-1]>=sstg:
            bigput_high[0]+=[sum(vars()[HO][0][(-(sstg)):])/sstg] 
            bigput_high[1]+=[sum(vars()[HO][1][(-(sstg)):])/sstg] 
            bigput_high[2]+=[sum(vars()[HO][2][(-(sstg)):])/sstg] # neste caso é para o shots/shotstarget/goals
        
        if fileN.iloc[i]['Lowest_Odd']=='H':   
            vars()[LO][0]+=[fileN.iloc[i]['HS']]
            vars()[LO][1]+=[fileN.iloc[i]['HST']]
            vars()[LO][2]+=[fileN.iloc[i]['FTHG']]
            vars()[HO][0]+=[fileN.iloc[i]['AS']]
            vars()[HO][1]+=[fileN.iloc[i]['AST']]
            vars()[HO][2]+=[fileN.iloc[i]['FTAG']]
        
        elif fileN.iloc[i]['Lowest_Odd']=='A': 
            vars()[LO][0]+=[fileN.iloc[i]['AS']]
            vars()[LO][1]+=[fileN.iloc[i]['AST']]
            vars()[LO][2]+=[fileN.iloc[i]['FTAG']]
            vars()[HO][0]+=[fileN.iloc[i]['HS']]
            vars()[HO][1]+=[fileN.iloc[i]['HST']]
            vars()[HO][2]+=[fileN.iloc[i]['FTHG']]

        #print(vars()[LO][6],LO)
          
          # # #  #   #    #     #      #       #       #       #   
        # # # Trata das listas da odds + altas mais baixas (coluna)
        if fileN.iloc[i]['Lowest_Odd']=='H':
            low_odd+=[fileN.iloc[i]['ODDH_Aver.']]
            high_odd+=[fileN.iloc[i]['ODDA_Aver.']]
        elif fileN.iloc[i]['Lowest_Odd']=='A':
            low_odd+=[fileN.iloc[i]['ODDA_Aver.']]
            high_odd+=[fileN.iloc[i]['ODDH_Aver.']]
        #   #    #    #    #    #     #     #     #     #     #
        
        ######## Trata da odd mais baixa com que o clube perdeu
        #if vars()[LO][-1]==0:
            #bigput_low[11]+=['To be defined']
        #elif vars()[LO][-1]>0:
        if fileN.iloc[i]['Lowest_Odd']=='H':
            #Equipa com odd + baixa (casa)
            if fileN.iloc[i]['ODDH_Aver.']<vars()[LO][11] and (fileN.iloc[i]['FTR']!='H'):
                if vars()[LO][-1]==0:
                    bigput_low[11]+=['To be defined']
                else:
                    bigput_low[11]+=[vars()[LO][11] if vars()[LO][11]!=10000 else 'To be defined']
                vars()[LO][11]=fileN.iloc[i]['ODDH_Aver.']
            else:
                if vars()[LO][-1]==0:
                    bigput_low[11]+=['To be defined']
                else:
                    bigput_low[11]+=[vars()[LO][11] if vars()[LO][11]!=10000 else 'To be defined']
            #Equipa com odd + alta (fora)
            if fileN.iloc[i]['ODDA_Aver.']<vars()[HO][11] and (fileN.iloc[i]['FTR']!='A'):
                if vars()[HO][-1]==0:
                    bigput_high[11]+=['To be defined']
                else:
                    bigput_high[11]+=[vars()[HO][11] if vars()[HO][11]!=10000 else 'To be defined']
                vars()[HO][11]=fileN.iloc[i]['ODDA_Aver.']
            else:
                if vars()[HO][-1]==0:
                    bigput_high[11]+=['To be defined']
                else:
                    bigput_high[11]+=[vars()[HO][11] if vars()[HO][11]!=10000 else 'To be defined']
                    
        
        #if vars()[HO][-1]==0:
            #bigput_high[11]+=['To be defined']
        #elif vars()[HO][-1]>0:
        if fileN.iloc[i]['Lowest_Odd']=='A':
            #Equipa com odd+ alta (casa)
            if fileN.iloc[i]['ODDH_Aver.']<vars()[HO][11] and (fileN.iloc[i]['FTR']!='H'):
                if vars()[HO][-1]==0:
                    bigput_high[11]+=['To be defined']
                else:
                    bigput_high[11]+=[vars()[HO][11] if vars()[HO][11]!=10000 else 'To be defined']
                vars()[HO][11]=fileN.iloc[i]['ODDH_Aver.']
            else:
                if vars()[HO][-1]==0:
                    bigput_high[11]+=['To be defined']
                else:
                    bigput_high[11]+=[vars()[HO][11] if vars()[HO][11]!=10000 else 'To be defined']
            #Equipa odd + baixa (fora)
            if fileN.iloc[i]['ODDA_Aver.']<vars()[LO][11] and (fileN.iloc[i]['FTR']!='A'):
                if vars()[LO][-1]==0:
                    bigput_low[11]+=['To be defined']
                else:
                    bigput_low[11]+=[vars()[LO][11] if vars()[LO][11]!=10000 else 'To be defined']
                vars()[LO][11]=fileN.iloc[i]['ODDA_Aver.']
            else:
                if vars()[LO][-1]==0:
                    bigput_low[11]+=['To be defined']
                else:
                    bigput_low[11]+=[vars()[LO][11] if vars()[LO][11]!=10000 else 'To be defined']
        
        #    #      #     #       #       #       #       #
        # Trata dos pontos nos últimos game_points
        if vars()[LO][-1]<game_points:
            bigput_low[12]+=[0]
        else:
            bigput_low[12]+=[sum(vars()[LO][12][(-(game_points)):])]
        
        if vars()[HO][-1]<game_points:
            bigput_high[12]+=[0]
        else:
            bigput_high[12]+=[sum(vars()[HO][12][(-(game_points)):])]
        
        if fileN.iloc[i]['Lowest_Odd']=='H':
            vars()[LO][12]+=[3 if fileN.iloc[i]['FTR']=='H' else 1 if fileN.iloc[i]['FTR']=='D' else 0]
            vars()[HO][12]+=[0 if fileN.iloc[i]['FTR']=='H' else 1 if fileN.iloc[i]['FTR']=='D' else 3]
        else:
            vars()[LO][12]+=[0 if fileN.iloc[i]['FTR']=='H' else 1 if fileN.iloc[i]['FTR']=='D' else 3]
            vars()[HO][12]+=[3 if fileN.iloc[i]['FTR']=='H' else 1 if fileN.iloc[i]['FTR']=='D' else 0]
            
        #    #        #         #     #      #     # 
       # Trata de dizer se a equipa com Odd + baixa joga Casa/Fora 
        if fileN.iloc[i]['Lowest_Odd']=='H':
            HA+=[h_a]
        else:
            HA+=[0]
       #####    #    #     #      #       #       #         #
    
        #    #    #   Trata do odd counter !  !   !   !      ! 
        
        
        if fileN.iloc[i]['Lowest_Odd']=='H':
            oddzz=round((fileN.iloc[i]['ODDH_Aver.'])*100)
            oddsput+=[odds[int((oddzz-100)//10)]]
        else:
            oddzz=round((fileN.iloc[i]['ODDA_Aver.'])*100)
            oddsput+=[odds[int((oddzz-100)//10)]]
                
        #counter
        if fileN.iloc[i]['Lowest_Odd']=='H':
            if fileN.iloc[i]['FTR']=='H': 
                if odds[int((oddzz-100)//10)]>0:
                    odds[int((oddzz-100)//10)]+=1
                else:
                    odds[int((oddzz-100)//10)]=1
            else: #se a equipa da casa odd + baixa não ganhar
                if odds[int((oddzz-100)//10)]>0:
                    odds[int((oddzz-100)//10)]=-1
                else:
                    odds[int((oddzz-100)//10)]-=1
                    
        else: # se a odd mais baixa for a equipa de fora
            if fileN.iloc[i]['FTR']=='H':
                if odds[int((oddzz-100)//10)]>0:
                    odds[int((oddzz-100)//10)]=-1
                else:
                    odds[int((oddzz-100)//10)]-=1
            else: #se a equipa de fora (odd + baixa ) ganhar
                if odds[int((oddzz-100)//10)]>0:
                    odds[int((oddzz-100)//10)]+=1
                else:
                    odds[int((oddzz-100)//10)]=1
    
    
    
        #   #    #   #   #       #      #      #  
        #   #    # Trata do counter das surpresas
        if vars()[LO][-1]==0:
            if fileN.iloc[i]['Lowest_Odd']=='H':
                if fileN.iloc[i]['ODDH_Aver.']<surprise_odd:
                    surpriseput+=[0]
                else:
                    surpriseput+=[no_surprise]
            # se a odd mais baixa for fora        
            else:
                if fileN.iloc[i]['ODDA_Aver.']<surprise_odd:
                    surpriseput+=[0]
                else:
                    surpriseput+=[no_surprise]
                
        elif vars()[LO][-1]>0:
            if fileN.iloc[i]['Lowest_Odd']=='H':
                if fileN.iloc[i]['ODDH_Aver.']<surprise_odd:
                    surpriseput+=[surprise]
                else:
                    surpriseput+=[no_surprise]
            # se a odd mais baixa for fora        
            else:
                if fileN.iloc[i]['ODDA_Aver.']<surprise_odd:
                    surpriseput+=[surprise]
                else:
                    surpriseput+=[no_surprise]
                    
        #counter
        if fileN.iloc[i]['Lowest_Odd']=='H':
            if fileN.iloc[i]['ODDH_Aver.']<surprise_odd:
                if fileN.iloc[i]['FTR']=='H':
                    if surprise>0:
                        surprise+=1
                    else:
                        surprise=1
                #se a equipa de casa (odd+baixa) não ganhar        
                else:
                    if surprise>0:
                        surprise=-1
                    else:
                        surprise-=1
        # se a odd mais baixa for fora        
        else:
            if fileN.iloc[i]['ODDA_Aver.']<surprise_odd:
                if fileN.iloc[i]['FTR']=='H':
                    if surprise>0:
                        surprise=-1
                    else:
                        surprise-=1
                #se a equipa de fora (odd+baixa) ganhar        
                else:
                    if surprise>0:
                        surprise+=1
                    else:
                        surprise=1
    
            
        # # # # # #   #    #   #   #   #   #   #
        # # # # Trata de saber qnts jogos teve fora nos últimos game_points jogos (+1 fora/+0 casa
        if vars()[LO][-1]<game_points:
            bigput_low[13]+=[0] #faz a média dos jogos já jogados, antes de chegar ao número de média pretendido
        else:
            bigput_low[13]+=[sum(vars()[LO][13][(-(game_points)):])]
            
        if vars()[HO][-1]==0:
            bigput_high[13]+=[0]
        elif 0<vars()[HO][-1]<game_points:
            bigput_high[13]+=[sum(vars()[HO][13])] #faz a média dos jogos já jogados, antes de chegar ao número de média pretendido
        else:
            bigput_high[13]+=[sum(vars()[HO][13][(-(game_points)):])]
            
        #preencher dados
        if fileN.iloc[i]['Lowest_Odd']=='H':
            vars()[LO][13]+=[0]
            vars()[HO][13]+=[1]
        else:
            vars()[LO][13]+=[1]
            vars()[HO][13]+=[0]
            
        #  #    #   #    #    #    #    #    #    #    # 
        #   # Trata do Won(1)/NotWon(0) em relação à odd + baixa
        if fileN.iloc[i]['Lowest_Odd']=='H':
            if fileN.iloc[i]['FTR']=='H':
                wonnotwon+=[1]
            else:
                wonnotwon+=[0]
        else:
            if fileN.iloc[i]['FTR']=='H':
                wonnotwon+=[0]
            else:
                wonnotwon+=[1]
            
        # # #    #   #   #   #   #   #   #  #   #   # 
        vars()[LO][-1]+=1 #faz o counter de cada clube andar
        vars()[HO][-1]+=1            
                
    fileC['Div']=fileN['Div']
    fileC['Date']=fileN['Date']
    fileC['Time']=fileN['Time']
    fileC['LO_Team']=l
    fileC['HO_Team']=h
    fileC['H/A']=HA
    if AwayLast:
        fileC['L_AwayLast_'+str(game_points)]=bigput_low[13]
        fileC['H_AwayLast_'+str(game_points)]=bigput_high[13]
    
    fileC['LowODD']=low_odd
    fileC['DrawODD']=fileN['ODDD_Aver.']
    fileC['HighODD']=high_odd
    if LowestLost:
        fileC['L_LowestLost']=bigput_low[11]
        fileC['H_LowestLost']=bigput_high[11]
    
    fileC['L_Points_'+str(game_points)]=bigput_low[12]
    fileC['H_Points_'+str(game_points)]=bigput_high[12]
    fileC['LoS'+str(sstg)]=bigput_low[0]
    fileC['HoS'+str(sstg)]=bigput_high[0]
    fileC['LoST'+str(sstg)]=bigput_low[1]
    fileC['HoST'+str(sstg)]=bigput_high[1]
    fileC['LoG'+str(sstg)]=bigput_low[2]
    fileC['HoG'+str(sstg)]=bigput_high[2]
    fileC['LoConceedAver_'+str(conceed_aver)]=bigput_low[3]
    fileC['HoConceedAver_'+str(conceed_aver)]=bigput_high[3]
    fileC['Lo_WinCount_']=bigput_low[4]
    fileC['Ho_WinCount_']=bigput_high[4]
    fileC['Lo_ScoresCount']=bigput_low[5]
    fileC['Ho_ScoresCount']=bigput_high[5]
    fileC['Lo_CleanSheet']=bigput_low[6]
    fileC['Ho_CleanSheet']=bigput_high[6]
    if SSTG:
        fileC['LoS']=bigput_low[7]
        fileC['HoS']=bigput_high[7]
        fileC['LoST']=bigput_low[8]
        fileC['HoST']=bigput_high[8]
        fileC['LoG']=bigput_low[9]
        fileC['HoG']=bigput_high[9]
        fileC['LoConcd']=bigput_low[10]
        fileC['HoConcd']=bigput_high[10]
        
    fileC['LeagueOddCounter']=oddsput
    if Surprise:
        fileC['SurprCount_'+str(surprise_odd)]=surpriseput
        
    fileC['Won/NotWon']=wonnotwon
    return fileC

In [124]:
def odd_allcounter(file):  #faz o count das odds qnd já juntámos várias ligas
    #Aqui não precisamos do ficheiro original, pq este já tem as odds
    
    limit=len(file.index)
    odds=[0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0] #odd counter (já vai ter counter negativos) (1,2.8,10)
    oddsput=[] #põe em coluna
    #for club in clubs:                 
    #    vars()[club]=[0] #agr só precisamos do counter do clube
    for i in range(limit):  
        oddzz = round((file.iloc[i]['LowODD'])*100)
        #põe os counter na lista para adicionar
        #print(i,'índice do ficheiro')
        #print(file.iloc[i]['LowODD'],'odd')
        #print(int((oddzz-100)//10),'indíce da lista')
        #print(oddzz,'odd*100')
        oddsput+=[odds[int((oddzz-100)//10)]]    

        #counter
        if file.iloc[i]['Won/NotWon']==1: 
            if odds[int((oddzz-100)//10)]>0:
                odds[int((oddzz-100)//10)]+=1
            else:
                odds[int((oddzz-100)//10)]=1
        else: #se a equipa da odd + baixa não ganhar
            if odds[int((oddzz-100)//10)]>0:
                odds[int((oddzz-100)//10)]=-1
            else:
                odds[int((oddzz-100)//10)]-=1
                
    file['ALLOddCounter']=oddsput
    return file    
        


In [171]:
def byodd_lion(path):
    file=pd.read_excel(path+'.xlsx',0)
    q=[[file]]
    for i in range(10,29,1):
        odd1=round(i/10,2)
        odd2=round(odd1+0.09,2)
        new=file.loc[(odd1<=file['LowODD']) & (file['LowODD']<=odd2)]
        q+=[[new,odd1,odd2]]
    with pd.ExcelWriter(path+".xlsx") as writer:
        for n, df in enumerate(q):
            if n==0:
                df[0].to_excel(writer, 'Lion_'+path, index=None)
            else:
                df[0].to_excel(writer, "%d_ODD_%s" %(df[1],df[2]) +"_"+path, index=None)
    writer.save()

In [177]:
byodd_lion('BigLion')

In [125]:
prem=pd.read_excel('PLTeste.xlsx',0)
lion=pd.DataFrame()
cc=findall_clubs('PLTeste',20)
bund=pd.read_excel('BundTeste.xlsx',0)
bundL=pd.DataFrame()
ccB=findall_clubs('BundTeste',18)
laliga=pd.read_excel('LLTeste.xlsx',0)
LLL=pd.DataFrame()
ccLL=findall_clubs('LLTeste',20)
SA=pd.read_excel('SATeste.xlsx',0)
SAL=pd.DataFrame()
ccSA=findall_clubs('SATeste',20)

In [126]:
ligue1=pd.read_excel('LTeste.xlsx',0)
Ll=pd.DataFrame()
cc1=findall_clubs('LTeste',20)
lp=pd.read_excel('LPTeste.xlsx',0)
LPl=pd.DataFrame()
cc2=findall_clubs('LPTeste',18)

In [127]:
#lion_SA=add_club_lion(SA,SAL,ccSA,SSTG=False,LowestLost=False,AwayLast=False,Surprise=False)

In [128]:
lion_l1=add_lion(ligue1,Ll,cc1)
lion_lp=add_lion(lp,LPl,cc2)

In [129]:
lion_prem=add_lion(prem,lion,cc)
lion_bund=add_lion(bund,bundL,ccB)
lion_ll=add_lion(laliga,LLL,ccLL)
lion_SA=add_lion(SA,SAL,ccSA)

In [90]:
pd.set_option('display.max_rows',2000)
pd.set_option('display.max_columns',1000)

In [172]:
BBiglion=pd.concat([lion_prem,lion_bund,lion_ll,lion_SA,lion_l1,lion_lp],sort=False)
BBiglion=BBiglion.sort_values(["Date", "Time"], ascending=[True,True])
BBiglion=BBiglion.reset_index(drop=True)

In [173]:
BBiglion=odd_allcounter(BBiglion)

In [174]:
BBiglion

Div       Date      Time             LO_Team             HO_Team  H/A  \
0      F1 2019-08-09     19:45                Lyon              Monaco    0   
1      E0 2019-08-09  20:00:00           Liverpool             Norwich   10   
2      P1 2019-08-09     20:30        Portimonense          Belenenses   10   
3      E0 2019-08-10  12:30:00            Man City            West Ham    0   
4      E0 2019-08-10  15:00:00         Bournemouth    Sheffield United   10   
5      E0 2019-08-10  15:00:00             Burnley         Southampton   10   
6      E0 2019-08-10  15:00:00             Everton      Crystal Palace    0   
7      E0 2019-08-10  15:00:00             Watford            Brighton   10   
8      F1 2019-08-10     16:30           Marseille               Reims   10   
9      P1 2019-08-10     16:30         Santa Clara           Famalicao   10   
10     E0 2019-08-10  17:30:00           Tottenham         Aston Villa   10   
11     F1 2019-08-10     19:00              Angers            Bordeaux   10   
12     F1 2019-08-10     19:00               Brest            Toulouse   10   
13     F1 2019-08-10     19:00          St Etienne               Dijon    0   
14     F1 2019-08-10     19:00         Montpellier              Rennes   10   
15     F1 2019-08-10     19:00                Nice              Amiens   10   
16     P1 2019-08-10     19:00               Porto         Gil Vicente    0   
17     P1 2019-08-10     21:30             Benfica      Pacos Ferreira   10   
18     F1 2019-08-11     14:00               Lille              Nantes   10   
19     E0 2019-08-11  14:00:00           Leicester              Wolves   10   
20     E0 2019-08-11  14:00:00             Arsenal           Newcastle    0   
21     F1 2019-08-11     16:00          Strasbourg                Metz   10   
22     P1 2019-08-11     16:00            Boavista                Aves   10   
23     E0 2019-08-11  16:30:00          Man United             Chelsea   10   
24     P1 2019-08-11     18:30           Sp Lisbon            Maritimo    0   
25     F1 2019-08-11     20:00            Paris SG               Nimes   10   
26     P1 2019-08-11     21:00            Sp Braga          Moreirense   10   
27     P1 2019-08-12     20:15             Setubal             Tondela   10   
28     D1 2019-08-16  19:30:00       Bayern Munich              Hertha   10   
29     F1 2019-08-16     19:45                Lyon              Angers   10   
30    SP1 2019-08-16     20:00           Barcelona          Ath Bilbao    0   
31     P1 2019-08-16     20:30             Rio Ave           Famalicao    0   
32     E0 2019-08-17  12:30:00             Arsenal             Burnley   10   
33     D1 2019-08-17  14:30:00            Dortmund            Augsburg   10   
34     D1 2019-08-17  14:30:00            Freiburg               Mainz   10   
35     D1 2019-08-17  14:30:00          Leverkusen           Paderborn   10   
36     D1 2019-08-17  14:30:00       Werder Bremen  Fortuna Dusseldorf   10   
37     D1 2019-08-17  14:30:00           Wolfsburg             FC Koln   10   
38     E0 2019-08-17  15:00:00         Aston Villa         Bournemouth   10   
39     E0 2019-08-17  15:00:00            Brighton            West Ham   10   
40     E0 2019-08-17  15:00:00             Everton             Watford   10   
41     E0 2019-08-17  15:00:00             Norwich           Newcastle   10   
42     E0 2019-08-17  15:00:00           Liverpool         Southampton    0   
43    SP1 2019-08-17     16:00         Real Madrid               Celta    0   
44     F1 2019-08-17     16:30              Nantes           Marseille   10   
45     P1 2019-08-17     16:30          Moreirense         Gil Vicente   10   
46     E0 2019-08-17  17:30:00            Man City           Tottenham   10   
47     D1 2019-08-17  17:30:00          M'gladbach          Schalke 04   10   
48    SP1 2019-08-17     18:00            Valencia            Sociedad   10   
49    SP1 2019-08-17     19:00               Eibar      

In [175]:
BBigLion=BBiglion[487:]

In [176]:
BBigLion.to_excel('BigLion.xlsx',index=False)

In [136]:
BBigLion.reset_index(drop=True)

Div       Date      Time             LO_Team             HO_Team  H/A  \
0      I1 2019-10-20     17:00               Parma               Genoa   10   
1      D1 2019-10-20  17:00:00          Schalke 04          Hoffenheim    0   
2     SP1 2019-10-20     17:30          Ath Bilbao          Valladolid   10   
3      I1 2019-10-20     19:45               Milan               Lecce   10   
4     SP1 2019-10-20     20:00             Sevilla             Levante   10   
5      F1 2019-10-20     20:00           Marseille          Strasbourg   10   
6      I1 2019-10-21     19:45          Fiorentina             Brescia    0   
7      E0 2019-10-21  20:00:00             Arsenal    Sheffield United    0   
8      D1 2019-10-25  19:30:00               Mainz             FC Koln   10   
9      I1 2019-10-25     19:45              Verona            Sassuolo   10   
10     F1 2019-10-25     19:45              Monaco              Nantes    0   
11    SP1 2019-10-25     20:00          Villarreal              Alaves   10   
12     E0 2019-10-25  20:00:00           Leicester         Southampton    0   
13     P1 2019-10-25     20:30             Rio Ave      Pacos Ferreira    0   
14     E0 2019-10-26  12:30:00            Man City         Aston Villa   10   
15     I1 2019-10-26     14:00            Juventus               Lecce    0   
16     D1 2019-10-26  14:30:00       Bayern Munich        Union Berlin   10   
17     D1 2019-10-26  14:30:00          RB Leipzig            Freiburg    0   
18     D1 2019-10-26  14:30:00              Hertha          Hoffenheim   10   
19     D1 2019-10-26  14:30:00           Paderborn  Fortuna Dusseldorf   10   
20     D1 2019-10-26  14:30:00            Dortmund          Schalke 04    0   
21    SP1 2019-10-26     15:00             Leganes            Mallorca   10   
22     E0 2019-10-26  15:00:00             Everton            Brighton    0   
23     E0 2019-10-26  15:00:00             Watford         Bournemouth   10   
24     E0 2019-10-26  15:00:00            West Ham    Sheffield United   10   
25     P1 2019-10-26     15:30          Belenenses                Aves   10   
26     P1 2019-10-26     15:30         Gil Vicente        Portimonense   10   
27     F1 2019-10-26     16:30               Lille            Bordeaux   10   
28     I1 2019-10-26     17:00               Inter               Parma   10   
29    SP1 2019-10-26     17:30          Valladolid               Eibar   10   
30     E0 2019-10-26  17:30:00             Chelsea             Burnley    0   
31     D1 2019-10-26  17:30:00          Leverkusen       Werder Bremen   10   
32     P1 2019-10-26     18:00             Setubal            Maritimo   10   
33     F1 2019-10-26     19:00               Brest               Dijon   10   
34     F1 2019-10-26     19:00                Lyon                Metz   10   
35     F1 2019-10-26     19:00         Montpellier              Angers   10   
36     F1 2019-10-26     19:00               Reims               Nimes   10   
37     F1 2019-10-26     19:00          Strasbourg                Nice   10   
38     I1 2019-10-26     19:45               Genoa             Brescia   10   
39    SP1 2019-10-26     20:00          Ath Madrid          Ath Bilbao   10   
40     P1 2019-10-26     20:30          Moreirense            Boavista   10   
41    SP1 2019-10-27     11:00            Sociedad               Celta    0   
42     I1 2019-10-27     11:30             Bologna           Sampdoria   10   
43    SP1 2019-10-27     13:00             Granada               Betis   10   
44     I1 2019-10-27     14:00            Atalanta             Udinese   10   
45     I1 2019-10-27     14:00              Napoli                Spal    0   
46     I1 2019-10-27     14:00              Torino            Cagliari   10   
47     F1 2019-10-27     14:00              Rennes            Toulouse   10   
48     E0 2019-10-27  14:00:00              Wolves           Newcastle    0   
49     D1 2019-10-27  14:30:00           Wolfsburg      